1) Pull these raw columns (annual t−1 values) — must have these for every stock
(Use the same accounting definitions across the universe; all variables are lagged by one year in the paper.)

Fundamentals / valuation

Price (close), 12-month high, 12-month low (for price_range).

Shares outstanding, MarketCap = price × shares.

Total Enterprise Value (TEV) = Market Cap + Total Debt − Cash & equivalents.

Book value of equity (book value) → Book-to-Market (B/M) = Book / MarketCap.

Free cash flow (FCF) = Operating cash flow − Capital expenditures (capex).

FCF/P (free cash flow yield) = FCF / MarketCap (paper calls FCF/P free cash flow yield). 
BCU Open Access

EBITDA, revenue, operating profit.

ROA = Net income / Total assets.

EBITDA margin = EBITDA / Revenue.

Assets (total assets) and YoY asset growth % = (Assets_t − Assets_{t−1}) / Assets_{t−1}.

EBITDA YoY growth % = (EBITDA_t − EBITDA_{t−1}) / EBITDA_{t−1}.

Net income, EPS (but note EPS not used as primary predictor).

Debt-to-equity, Total debt, Interest expense (for coverage).

EV/EBITDA, EV/Sales (optional).

Insiders transactions (sum net buys/sells last 12 months).

Institutional ownership %, analyst coverage (optional).

Price / technical

1-month, 3-month, 6-month returns (monthly totals), lagged 1 month.

price_range = (current_price − 12m_low) / (12m_high − 12m_low) (0–1 scaled; paper uses 0–100%). 
BCU Open Access

Macro

S&P500 annual return (or RM), 3-month T-bill (risk-free), Fed funds rate history (for constructing interest_env dummy: 1 if Fed rate rising this year, else 0). 
BCU Open Access

2) Derived signals & exact formulas (implement these exactly)
FCF/P

FCF = Cash from operations − CapEx.

FCF_yield = FCF / MarketCap (use lagged MarketCap at rebalance date).

Winsorize FCF_yield at 1st and 99th percentiles (or cap extreme outliers). The paper treats this as one of the highest-impact variables. 
BCU Open Access

Book-to-Market (B/M)

B/M = BookValuePerShare × Shares / MarketCap (or BookValue / MarketCap). Use common definitions and lag. 
BCU Open Access

Size (TEV)

TEV = MarketCap + TotalDebt − Cash. Use ln(TEV) in models or to rank. Paper finds ln_TEV has a strongly negative coefficient. Use TEV lagged. 
BCU Open Access

Inv_dummy (critical) — create exactly as:

Inv_dummy = 1 if YoY asset growth (%) > YoY EBITDA growth (%) for the same pair of years; else 0.

Paper: Inv_dummy coefficient ≈ −22.789 in upgraded FE model (huge negative effect). Use this as a hard exclude (or large negative score). 
BCU Open Access

Profitability

ROA = NetIncome / TotalAssets (use lag). Paper prefers ROA in dynamic models (coefficients ~0.4–1.9). Also compute EBITDA margin = EBITDA / Revenue; use either as profitability signals. 
BCU Open Access
+1

Price_range

price_range = (Price_now − 12m_low) / (12m_high − 12m_low) ∈ [0,1]. Higher price_range (close to 12m high) → lower next-year returns per paper. Use threshold logic (below). 
BCU Open Access

Momentum

1m_return, 3m_return, 6m_return. Paper: 1-month sometimes positive, but 3–6 month momentum negative (quick reversals). Use nuance in scoring. 
BCU Open Access

Interest environment dummy

interest_env = 1 if Fed funds rate at year t > Fed funds rate at year t−1 (Fed rate rising year), else 0. Paper finds rising Fed rate → multibagger returns depressed by ~8–12 ppt. Use as portfolio size / risk control. 
BCU Open Access

3) Hard filters (exclude these immediately) — follow the paper’s strong findings
(These are must apply before scoring.)

Inv_dummy == 1 → EXCLUDE (paper: huge negative effect ≈ −22.8 p.p.). If you prefer not to exclude, apply a heavyweight penalty (score −2 or weight multiplier). 
BCU Open Access

Remove firms with missing or zero MarketCap / TEV data.

Remove micro-penny, illiquid names — set min ADV (average daily volume) threshold (e.g., 50k–100k shares/day) and/or min price (e.g., $1) to avoid stale quotes and microstructure issues. (Paper uses listed major exchanges.)

If using P/E at all: only for firms with positive, stable earnings for last 2 yrs (paper: P/E is unreliable and was avoided). Prefer FCF/P/BM instead. 
BCU Open Access

4) +1 / 0 / −1 rules (exact percentile cutoffs & fallbacks)
Use annual rebalance, compute percentiles cross-sectionally each rebalance date, convert to −1/0/+1 per metric.

Primary signals (high weight):

FCF/P (lagged)

top 20% → +1

middle 20–80% → 0

bottom 20% → −1.
(Paper: FCF/P has one of the largest positive coefficient ranges.) 
BCU Open Access

Book-to-Market (B/M) (lagged)

top 30% → +1

middle 30–70% → 0

bottom 30% → −1. 
BCU Open Access

Size (TEV, lagged)

bottom 30% TEV (smallest) → +1

middle 30–70% → 0

top 30% → −1. 
BCU Open Access

Secondary signals (moderate weight):

ROA or EBITDA margin (lagged)

= 75th pctile → +1

25–75th → 0

<= 25th → −1. 
BCU Open Access

price_range (lagged) (distance to 12m high)

price_range >= 0.85 → −1 (too close to high)

price_range <= 0.35 → +1 (near low)

otherwise → 0. 
BCU Open Access

Momentum (nuance):

1-month return: if in top 20% AND price_range < 0.85 → +1; if 1-month in bottom 20% → −1 (optional).

3-6 month return: if top 20% → −1 (paper finds medium-term reversal). 
BCU Open Access

Tertiary / tie-breakers (low weight)

Insider net buying (12mo): top 33% → +1, bottom 33% → −1 (paper treats this as supplemental).

Debt: extreme high leverage (>= 95th percentile) → −1 (use as risk control, not main predictor). 
BCU Open Access

5) Scoring & weights (concrete formula you can code now)
Option A — Coefficient-informed weighted score (recommended; aligns with paper)

Normalize each metric to percentile, then convert to −1/0/+1 per above, multiply by weights and sum.

Suggested weights (sum absolute weights = 1):

FCF/P: 0.30

B/M: 0.20

TEV size: 0.15

Inv_dummy penalty: 0.15 (if Inv_dummy==1, subtract 2×0.15 or reject)

ROA / EBITDA: 0.10

price_range/momentum combo: 0.07

insiders / debt tie-breaker: 0.03

Score = 0.30sig_FCF + 0.20sig_BM + 0.15sig_size − 0.15(Inv_dummy?1:0) + 0.10sig_ROA + 0.07sig_price_mom + 0.03*sig_misc

Interpretation:

Top decile of scores → pick for portfolio; or take top N by score.

If Inv_dummy==1: either exclude or force score < threshold (paper supports strong exclusion). 
BCU Open Access

Option B — Regression-replication score

If you prefer to replicate regression outputs exactly, I can export the numeric coefficients (Table 3–5) and you build a linear predictor using the paper’s coefficients (BUT beware of overfitting / need for same variable definitions). I can export those now if you want. 
BCU Open Access
+1

6) Backtest design specifics (do this exactly — avoids common traps)
Data handling

All fundamentals & ratios use t−1 (lagged) values at each rebalance. No inside info. 
BCU Open Access

Winsorize fundamentals at 1st/99th pctile or use log transforms (e.g., ln(TEV)).

Impute missing noncritical data conservatively (e.g., treat missing FCF as 0 only if clearly missing; better: drop).

Survivorship bias: use historical constituents or CRSP/Compustat with delisting returns included. Include delisting returns as −100% if necessary.

Transaction costs / spread: model realistic slippage (0.25–1% per trade depending on size/liquidity) and commissions. Small caps are expensive.

Liquidity filter: min ADV and minimum market cap threshold.

Rebalance frequency: annual (paper uses annual dependent variable). You can test semi-annual as a sensitivity but be cautious (momentum reversal). 
BCU Open Access

Portfolio construction

Equal weight the selected top N (paper doesn’t prescribe exact sizing). Equal weighting reduces single-name risk. Alternatively use score-weighted sizing (cap sum weights positive only).

Position limit: max 3–5% of portfolio per position to reduce idiosyncratic risk.

Macro overlay (interest_env): if Fed is rising (interest_env==1) reduce total exposure by e.g., 20–40% (paper: interest_env depresses returns by ~8–12 p.p.). 
BCU Open Access

Evaluation metrics

Annualized return, volatility, Sharpe, Max drawdown, CAGR vs S&P500, and long-short alpha vs Fama-French 5 factors. Compute information ratio and hit-rate for outperforming the market.

Test bootstrap and out-of-sample (train on 2000–2018, test 2019–2024) or rolling expanding window to check stability.

Diagnostics & robustness

Check multicollinearity (VIF) if you use regression weighting.

Run placebo tests: random long portfolios, or keep Inv_dummy but flip signs.

Test subperiods and sector neutral variants (some sectors dominated). The blog coverage of this paper suggested IT, Industrials, Consumer Discretionary, Healthcare and Financials are common multibagger sectors — you may want a sector cap to avoid sector concentration. 
100 Bagger Hunting

7) Edge cases / gotchas from the paper (so your model isn't lying)
P/E is unreliable for small and loss firms — avoid as core metric. Use FCF/P or B/M instead. 
BCU Open Access

Earnings growth / EPS growth is not predictive of future multibagger returns in the paper — don’t overweight EPS growth. 
BCU Open Access

Momentum reversals: 1-month may help, 3–6 month tends to hurt next-year returns. Don’t blindly follow 6-month momentum. 
BCU Open Access

Biases in coefficient magnitudes: different estimators produce different magnitudes (ln_TEV ranges, FCF/P ranges). Use percentiles and robustness checks instead of hard coefficient replication unless you match variable definitions exactly. 
BCU Open Access
+1

8) Immediate checklist you can implement now (copy/paste)
Data columns to fetch (annual, t−1): Price, Shares, MarketCap, TotalDebt, Cash, BookValue, TotalAssets, Revenue, EBITDA, OperatingCashFlow, CapEx, NetIncome, InsiderNetBuy12m, Adv30d, AnalystCoverage, sector, FedFundsRate.

Derived features (code formulas):

TEV = MarketCap + TotalDebt − Cash

B/M = BookValue / MarketCap

FCF = OperatingCashFlow − CapEx; FCF/P = FCF / MarketCap (winsorize)

ROA = NetIncome / TotalAssets; EBITDA_margin = EBITDA / Revenue

AssetGrowthYoY = (Assets_t − Assets_{t−1})/Assets_{t−1}

EBITDAgrowthYoY = (EBITDA_t − EBITDA_{t−1})/EBITDA_{t−1}

Inv_dummy = 1 if AssetGrowthYoY > EBITDAgrowthYoY else 0

price_range = (Price − 12m_low) / (12m_high − 12m_low)

interest_env = 1 if FedFunds_t > FedFunds_{t−1} else 0

Scoring code (pseudo):

Apply hard filters (liquidity, Inv_dummy==0, min price).

Compute percentiles for FCF/P, B/M, TEV (lower TEV better), ROA, price_range, momentum.

Convert to −1/0/+1 by thresholds above.

Compute weighted sum with weights in Section 5.

Rank and pick top N (or top X%); equal weight and rebalance annually.

Apply macro overlay if interest_env == 1 (reduce exposure 20–40%).

In [53]:
# GS13VDSMCEAZQL7C

list of symbols are producing: timeseries of income statement, balance sheet, and cash flow statement from this take:


In [54]:
import pandas as pd
import numpy as np
import requests
import time
from IPython.display import display, Markdown

def fetch_alpha_vantage_data(function, symbol, api_key):

    base_url = "https://www.alphavantage.co/query?"
    url = (
        f"{base_url}function={function}&symbol={symbol}"
        f"&apikey={api_key}"
    )

    try:
        # Make the GET request to the API.
        response = requests.get(url)
        
        # Raise an HTTPError for bad responses (4xx or 5xx status codes).
        response.raise_for_status()

        # Parse the JSON response.
        data = response.json()

        # Check for specific error messages from the Alpha Vantage API itself.
        if 'Error Message' in data:
            raise Exception(f"Alpha Vantage API error: {data['Error Message']}")
        if 'Information' in data and 'Thank you for using Alpha Vantage' in data['Information']:
            print("Note: API call frequency limit reached. Waiting and retrying...")
            # Implement a simple delay if the user hits the rate limit.
            # This is a basic retry mechanism.
            time.sleep(16) # Alpha Vantage free tier is 5 calls per minute (12 seconds per call)
            return fetch_alpha_vantage_data(function, symbol, api_key)

        return data

    except requests.exceptions.RequestException as e:
        # Catch any network-related errors.
        raise Exception(f"Network request failed: {e}")
    except ValueError as e:
        # Catch JSON decoding errors.
        raise Exception(f"Failed to decode JSON from response: {e}")

def convert_to_timeseries_df(data, statement_type):
    # Only process quarterly reports
    if not data or 'quarterlyReports' not in data:
        print(f"No quarterly reports found for {statement_type}")
        return pd.DataFrame()
    
    print(f"Quarterly reports available: {len(data['quarterlyReports'])}")
    
    # Convert quarterly reports to DataFrame
    df_quarterly = pd.DataFrame(data['quarterlyReports'])
    
    if df_quarterly.empty:
        return pd.DataFrame()
    
    # Mark as quarterly data
    df_quarterly['reportType'] = 'Quarterly'
    
    # Convert fiscal date to datetime and set as index
    df_quarterly['fiscalDateEnding'] = pd.to_datetime(df_quarterly['fiscalDateEnding'])
    df_quarterly = df_quarterly.set_index('fiscalDateEnding')
    
    # Convert all numeric columns (except reportType)
    numeric_columns = df_quarterly.columns.drop(['reportType'], errors='ignore')
    for col in numeric_columns:
        df_quarterly[col] = pd.to_numeric(df_quarterly[col], errors='coerce')
    
    # Sort by date (oldest first) to see historical range
    df_quarterly = df_quarterly.sort_index()
    
    return df_quarterly

def convert_price_data_to_df(data, symbol):
    """Convert Alpha Vantage price data to DataFrame"""
    if not data:
        print(f"No price data found for {symbol}")
        return pd.DataFrame()
    
    # Check for monthly time series data
    time_series_key = None
    for key in data.keys():
        if 'Time Series' in key or 'Monthly' in key:
            time_series_key = key
            break
    
    if not time_series_key:
        print(f"No time series data found for {symbol}")
        return pd.DataFrame()
    
    # Convert to DataFrame
    price_data = data[time_series_key]
    df = pd.DataFrame.from_dict(price_data, orient='index')
    
    # Convert index to datetime
    df.index = pd.to_datetime(df.index)
    df.index.name = 'date'
    
    # Convert all columns to numeric and rename them
    column_mapping = {
        '1. open': 'open',
        '2. high': 'high', 
        '3. low': 'low',
        '4. close': 'close',
        '5. volume': 'volume',
        '1. Open': 'open',
        '2. High': 'high',
        '3. Low': 'low', 
        '4. Close': 'close',
        '5. Volume': 'volume'
    }
    
    df = df.rename(columns=column_mapping)
    
    # Convert to numeric
    for col in df.columns:
        df[col] = pd.to_numeric(df[col], errors='coerce')
    
    # Sort by date (oldest first)
    df = df.sort_index()
    
    return df

def calculate_market_cap_timeseries(price_df, overview_data, balance_sheet_df=None):
    """Calculate market cap time series using price and historical shares outstanding from balance sheet"""
    if price_df.empty:
        return pd.DataFrame()
    
    # Create market cap DataFrame
    market_cap_df = pd.DataFrame(index=price_df.index)
    market_cap_df['close_price'] = price_df['close']
    
    # Try to use quarterly shares outstanding from balance sheet first
    if balance_sheet_df is not None and not balance_sheet_df.empty:
        if 'commonStockSharesOutstanding' in balance_sheet_df.columns:
            shares_ts = balance_sheet_df['commonStockSharesOutstanding'].dropna()
            
            if not shares_ts.empty:
                print(f"Using quarterly shares outstanding data from {shares_ts.index.min().strftime('%Y-%m-%d')} to {shares_ts.index.max().strftime('%Y-%m-%d')}")
                
                # Forward fill shares outstanding for monthly price data
                # This assumes shares outstanding remains constant between quarterly reports
                market_cap_df['shares_outstanding'] = np.nan
                
                # Fill in the quarterly values
                for date, shares in shares_ts.items():
                    # Find the closest price date to or after the fiscal date
                    mask = market_cap_df.index >= date
                    if mask.any():
                        first_valid_idx = market_cap_df.index[mask][0]
                        market_cap_df.loc[market_cap_df.index >= first_valid_idx, 'shares_outstanding'] = shares
                
                # Backward fill for dates before the first quarterly report
                market_cap_df['shares_outstanding'] = market_cap_df['shares_outstanding'].bfill()
                
                # Forward fill any remaining NaN values
                market_cap_df['shares_outstanding'] = market_cap_df['shares_outstanding'].ffill()
                
                # Calculate market cap
                market_cap_df['market_cap'] = market_cap_df['close_price'] * market_cap_df['shares_outstanding']
                
                return market_cap_df
    
    # Fallback to overview data if balance sheet doesn't have the data
    shares_outstanding = None
    if 'SharesOutstanding' in overview_data:
        shares_outstanding = pd.to_numeric(overview_data['SharesOutstanding'], errors='coerce')
    
    if shares_outstanding is None or pd.isna(shares_outstanding):
        print("Warning: No valid shares outstanding data found in balance sheet or overview")
        return pd.DataFrame()
    
    print("Warning: Using constant shares outstanding from overview data (limited historical accuracy)")
    market_cap_df['shares_outstanding'] = shares_outstanding
    market_cap_df['market_cap'] = market_cap_df['close_price'] * market_cap_df['shares_outstanding']
    
    return market_cap_df

In [55]:


symbols = [
    "AAPL", "MSFT", "GOOG", "AMZN", "NVDA", "META", "TSLA", "PEP", "AVGO",
    "COST", "CSCO", "ADBE", "NFLX", "TMUS", "TXN", "CMCSA", "QCOM", "INTC", "HON",
    "AMD", "AMGN", "INTU", "ISRG", "BKNG", "MDLZ", "ADI", "LRCX", "VRTX", "MU",
    "AMAT", "SBUX", "GILD", "MRNA", "ADP", "PANW", "FISV", "CSX", "REGN", "MNST",
    "KLAC", "MAR", "NXPI", "ORLY", "ADSK", "MCHP", "AEP", "KDP", "SNPS",
    "FTNT", "IDXX", "LULU", "EXC", "CTAS", "PAYX", "XEL", "PCAR", "ODFL", "VRSK",
    "WBA", "CDNS", "AZN", "DLTR", "EBAY", "BIIB", "ROST", "CRWD", "CHTR",
    "FAST", "PDD", "ANSS", "MRVL", "TEAM", "WDAY", "BKR", "DDOG", "ZS", "CEG",
    "KHC", "VRSN", "CTSH", "SWKS", "OKTA", "EA", "LCID", "BIDU", "ALGN",
    "MELI", "JD", "LI", "NTES", "ASML", "DXCM", "CPRT"
]

# Reuse existing helper
fetch = fetch_alpha_vantage_data
API_KEY = '1VWXIAX2LM6F6WV0'

company_data = {}
for sym in symbols:
    try:
        print(f"Fetching data for {sym}...")
        ov = fetch('OVERVIEW', sym, API_KEY)
        is_ = fetch('INCOME_STATEMENT', sym, API_KEY)
        bs = fetch('BALANCE_SHEET', sym, API_KEY)
        cf = fetch('CASH_FLOW', sym, API_KEY)
        
        # Fetch price data (using TIME_SERIES_MONTHLY for maximum historical data)
        print(f"Fetching price data for {sym}...")
        price_data = fetch('TIME_SERIES_MONTHLY', sym, API_KEY)
        
        company_data[sym] = {
            'overview': ov, 
            'income': is_, 
            'bs': bs, 
            'cf': cf,
            'price': price_data
        }
    except Exception as e:
        company_data[sym] = {'error': str(e)}

# Convert to time series DataFrames
print("\n" + "="*80)
print("CONVERTING TO TIME SERIES DATAFRAMES")
print("="*80)

financial_dataframes = {}
price_dataframes = {}
market_cap_dataframes = {}

for sym in symbols:
    if 'error' in company_data[sym]:
        print(f"\nSkipping {sym} due to error: {company_data[sym]['error']}")
        continue
    
    financial_dataframes[sym] = {}
    
    print(f"\n{'='*20} {sym} FINANCIAL TIME SERIES {'='*20}")
    
    # Income Statement Time Series
    print(f"\n--- {sym} INCOME STATEMENT TIME SERIES ---")
    income_df = convert_to_timeseries_df(company_data[sym]['income'], 'income')
    if not income_df.empty:
        financial_dataframes[sym]['income_statement'] = income_df
        print(f"Shape: {income_df.shape}")
        print(f"Date range: {income_df.index.min().strftime('%Y-%m-%d')} to {income_df.index.max().strftime('%Y-%m-%d')}")
        print(f"Columns: {list(income_df.columns)}")
        print("\nSample data (last 3 periods):")
        display(income_df.tail(3))
    else:
        print("No income statement data available")
    
    # Balance Sheet Time Series
    print(f"\n--- {sym} BALANCE SHEET TIME SERIES ---")
    bs_df = convert_to_timeseries_df(company_data[sym]['bs'], 'balance_sheet')
    if not bs_df.empty:
        financial_dataframes[sym]['balance_sheet'] = bs_df
        print(f"Shape: {bs_df.shape}")
        print(f"Date range: {bs_df.index.min().strftime('%Y-%m-%d')} to {bs_df.index.max().strftime('%Y-%m-%d')}")
        print(f"Columns: {list(bs_df.columns)}")
        print("\nSample data (last 3 periods):")
        display(bs_df.tail(3))
    else:
        print("No balance sheet data available")
    
    # Cash Flow Time Series
    print(f"\n--- {sym} CASH FLOW TIME SERIES ---")
    cf_df = convert_to_timeseries_df(company_data[sym]['cf'], 'cash_flow')
    if not cf_df.empty:
        financial_dataframes[sym]['cash_flow'] = cf_df
        print(f"Shape: {cf_df.shape}")
        print(f"Date range: {cf_df.index.min().strftime('%Y-%m-%d')} to {cf_df.index.max().strftime('%Y-%m-%d')}")
        print(f"Columns: {list(cf_df.columns)}")
        print("\nSample data (last 3 periods):")
        display(cf_df.tail(3))
    else:
        print("No cash flow data available")
    
    # Price Data Time Series
    print(f"\n--- {sym} PRICE DATA TIME SERIES ---")
    price_df = convert_price_data_to_df(company_data[sym]['price'], sym)
    if not price_df.empty:
        price_dataframes[sym] = price_df
        print(f"Shape: {price_df.shape}")
        print(f"Date range: {price_df.index.min().strftime('%Y-%m-%d')} to {price_df.index.max().strftime('%Y-%m-%d')}")
        print(f"Columns: {list(price_df.columns)}")
        print("\nSample data (last 5 months):")
        display(price_df.tail(5))
        
        # Market Cap Time Series (using balance sheet shares outstanding)
        print(f"\n--- {sym} MARKET CAP TIME SERIES ---")
        balance_sheet_for_shares = bs_df if not bs_df.empty else None
        market_cap_df = calculate_market_cap_timeseries(price_df, company_data[sym]['overview'], balance_sheet_for_shares)
        if not market_cap_df.empty:
            market_cap_dataframes[sym] = market_cap_df
            print(f"Shape: {market_cap_df.shape}")
            print(f"Date range: {market_cap_df.index.min().strftime('%Y-%m-%d')} to {market_cap_df.index.max().strftime('%Y-%m-%d')}")
            print(f"Current market cap: ${market_cap_df['market_cap'].iloc[-1]:,.0f}")
            print("\nSample data (last 5 months):")
            display(market_cap_df.tail(5))
        else:
            print("Could not calculate market cap data")
    else:
        print("No price data available")

print("\n" + "="*80)
print("SUMMARY OF ALL TIME SERIES DATA")
print("="*80)

for sym in symbols:
    print(f"\n{sym}:")
    
    # Financial statements
    if sym in financial_dataframes:
        for statement_type, df in financial_dataframes[sym].items():
            print(f"  {statement_type}: {df.shape[0]} periods, {df.shape[1]} metrics")
            print(f"    Date range: {df.index.min().strftime('%Y-%m-%d')} to {df.index.max().strftime('%Y-%m-%d')}")
    
    # Price data
    if sym in price_dataframes:
        df = price_dataframes[sym]
        print(f"  price_data: {df.shape[0]} months, {df.shape[1]} metrics")
        print(f"    Date range: {df.index.min().strftime('%Y-%m-%d')} to {df.index.max().strftime('%Y-%m-%d')}")
    
    # Market cap data
    if sym in market_cap_dataframes:
        df = market_cap_dataframes[sym]
        print(f"  market_cap: {df.shape[0]} months")
        print(f"    Date range: {df.index.min().strftime('%Y-%m-%d')} to {df.index.max().strftime('%Y-%m-%d')}")
        print(f"    Latest market cap: ${df['market_cap'].iloc[-1]:,.0f}")

# Access individual DataFrames like this:
# financial_dataframes['AAPL']['income_statement']
# price_dataframes['AAPL']
# market_cap_dataframes['AAPL']

Fetching data for AAPL...
Fetching price data for AAPL...
Fetching data for MSFT...
Fetching price data for MSFT...
Fetching data for GOOG...
Fetching price data for GOOG...
Fetching data for AMZN...
Fetching price data for AMZN...
Fetching data for NVDA...
Fetching price data for NVDA...
Fetching data for META...
Fetching price data for META...
Fetching data for TSLA...
Fetching price data for TSLA...
Fetching data for PEP...
Fetching price data for PEP...
Fetching data for AVGO...
Fetching price data for AVGO...
Fetching data for COST...
Fetching price data for COST...
Fetching data for CSCO...
Fetching price data for CSCO...
Fetching data for ADBE...
Fetching price data for ADBE...
Fetching data for NFLX...
Fetching price data for NFLX...
Fetching data for TMUS...
Fetching price data for TMUS...
Fetching data for TXN...
Fetching price data for TXN...
Fetching data for CMCSA...
Fetching price data for CMCSA...
Fetching data for QCOM...
Fetching price data for QCOM...
Fetching data fo

reportedCurrency  grossProfit  totalRevenue  costOfRevenue  \
fiscalDateEnding                                                               
2024-12-31                     NaN  58275000000  124300000000    66025000000   
2025-03-31                     NaN  44867000000   95359000000    50492000000   
2025-06-30                     NaN  43718000000   94036000000    50318000000   

                  costofGoodsAndServicesSold  operatingIncome  \
fiscalDateEnding                                                
2024-12-31                       66025000000      42832000000   
2025-03-31                       50492000000      29589000000   
2025-06-30                       50318000000      28202000000   

                  sellingGeneralAndAdministrative  researchAndDevelopment  \
fiscalDateEnding                                                            
2024-12-31                             7175000000              8268000000   
2025-03-31                             6728000000              8550000000   
2025-06-30                             6650000000              8866000000   

                  operatingExpenses  investmentIncomeNet  ...  \
fiscalDateEnding                                          ...   
2024-12-31              15443000000                  NaN  ...   
2025-03-31              15278000000                  NaN  ...   
2025-06-30              15516000000                  NaN  ...   

                  depreciationAndAmortization  incomeBeforeTax  \
fiscalDateEnding                                                 
2024-12-31                       3.080000e+09      42584000000   
2025-03-31                       2.661000e+09      29310000000   
2025-06-30                                NaN      28031000000   

                  incomeTaxExpense  interestAndDebtExpense  \
fiscalDateEnding                                             
2024-12-31              6254000000                     NaN   
2025-03-31              4530000000                     NaN   
2025-06-30              4597000000                     NaN   

                  netIncomeFromContinuingOperations  \
fiscalDateEnding                                      
2024-12-31                              36330000000   
2025-03-31                              24780000000   
2025-06-30                              23434000000   

                  comprehensiveIncomeNetOfTax          ebit       ebitda  \
fiscalDateEnding                                                           
2024-12-31                                NaN  4.283200e+10  45912000000   
2025-03-31                                NaN  2.958900e+10  32250000000   
2025-06-30                                NaN           NaN  28031000000   

                    netIncome  reportType  
fiscalDateEnding                           
2024-12-31        36330000000   Quarterly  
2025-03-31        24780000000   Quarterly  
2025-06-30        23434000000   Quarterly  

[3 rows x 26 columns]


--- AAPL BALANCE SHEET TIME SERIES ---
Quarterly reports available: 81
Shape: (81, 38)
Date range: 2005-06-30 to 2025-06-30
Columns: ['reportedCurrency', 'totalAssets', 'totalCurrentAssets', 'cashAndCashEquivalentsAtCarryingValue', 'cashAndShortTermInvestments', 'inventory', 'currentNetReceivables', 'totalNonCurrentAssets', 'propertyPlantEquipment', 'accumulatedDepreciationAmortizationPPE', 'intangibleAssets', 'intangibleAssetsExcludingGoodwill', 'goodwill', 'investments', 'longTermInvestments', 'shortTermInvestments', 'otherCurrentAssets', 'otherNonCurrentAssets', 'totalLiabilities', 'totalCurrentLiabilities', 'currentAccountsPayable', 'deferredRevenue', 'currentDebt', 'shortTermDebt', 'totalNonCurrentLiabilities', 'capitalLeaseObligations', 'longTermDebt', 'currentLongTermDebt', 'longTermDebtNoncurrent', 'shortLongTermDebtTotal', 'otherCurrentLiabilities', 'otherNonCurrentLiabilities', 'totalShareholderEquity', 'treasuryStock', 'retainedEarnings', 'commonStock', 'commonStockSharesOu

reportedCurrency   totalAssets  totalCurrentAssets  \
fiscalDateEnding                                                       
2024-12-31                     NaN  344085000000        133240000000   
2025-03-31                     NaN  331233000000        118674000000   
2025-06-30                     NaN  331495000000        122491000000   

                  cashAndCashEquivalentsAtCarryingValue  \
fiscalDateEnding                                          
2024-12-31                                  30299000000   
2025-03-31                                  28162000000   
2025-06-30                                  30465000000   

                  cashAndShortTermInvestments   inventory  \
fiscalDateEnding                                            
2024-12-31                        30299000000  6911000000   
2025-03-31                        28162000000  6269000000   
2025-06-30                        30465000000  5925000000   

                  currentNetReceivables  totalNonCurrentAssets  \
fiscalDateEnding                                                 
2024-12-31                  59306000000           210845000000   
2025-03-31                  49798000000           212559000000   
2025-06-30                  46835000000           209004000000   

                  propertyPlantEquipment  \
fiscalDateEnding                           
2024-12-31                  4.606900e+10   
2025-03-31                  4.687600e+10   
2025-06-30                  4.850800e+10   

                  accumulatedDepreciationAmortizationPPE  ...  \
fiscalDateEnding                                          ...   
2024-12-31                                           NaN  ...   
2025-03-31                                           NaN  ...   
2025-06-30                                           NaN  ...   

                  longTermDebtNoncurrent  shortLongTermDebtTotal  \
fiscalDateEnding                                                   
2024-12-31                           NaN            9.679900e+10   
2025-03-31                           NaN            9.818600e+10   
2025-06-30                           NaN            1.016980e+11   

                  otherCurrentLiabilities  otherNonCurrentLiabilities  \
fiscalDateEnding                                                        
2024-12-31                    61151000000                4.900600e+10   
2025-03-31                    61849000000                4.130000e+10   
2025-06-30                    62499000000                4.211500e+10   

                  totalShareholderEquity  treasuryStock  retainedEarnings  \
fiscalDateEnding                                                            
2024-12-31                   66758000000            NaN      -11221000000   
2025-03-31                   66796000000            NaN      -15552000000   
2025-06-30                   65830000000            NaN      -17607000000   

                  commonStock  commonStockSharesOutstanding  reportType  
fiscalDateEnding                                                         
2024-12-31        84768000000                   15150865000   Quarterly  
2025-03-31        88711000000                   15056133000   Quarterly  
2025-06-30        89806000000                   14948179000   Quarterly  

[3 rows x 38 columns]


--- AAPL CASH FLOW TIME SERIES ---
Quarterly reports available: 81
Shape: (81, 29)
Date range: 2005-06-30 to 2025-06-30
Columns: ['reportedCurrency', 'operatingCashflow', 'paymentsForOperatingActivities', 'proceedsFromOperatingActivities', 'changeInOperatingLiabilities', 'changeInOperatingAssets', 'depreciationDepletionAndAmortization', 'capitalExpenditures', 'changeInReceivables', 'changeInInventory', 'profitLoss', 'cashflowFromInvestment', 'cashflowFromFinancing', 'proceedsFromRepaymentsOfShortTermDebt', 'paymentsForRepurchaseOfCommonStock', 'paymentsForRepurchaseOfEquity', 'paymentsForRepurchaseOfPreferredStock', 'dividendPayout', 'dividendPayoutCommonStock', 'dividendPayoutPreferredStock', 'proceedsFromIssuanceOfCommonStock', 'proceedsFromIssuanceOfLongTermDebtAndCapitalSecuritiesNet', 'proceedsFromIssuanceOfPreferredStock', 'proceedsFromRepurchaseOfEquity', 'proceedsFromSaleOfTreasuryStock', 'changeInCashAndCashEquivalents', 'changeInExchangeRate', 'netIncome', 'reportType']

Sam

...


--- CPRT PRICE DATA TIME SERIES ---
Shape: (309, 5)
Date range: 1999-12-31 to 2025-08-08
Columns: ['open', 'high', 'low', 'close', 'volume']

Sample data (last 5 months):


open    high      low   close     volume
date                                                 
2025-04-30  56.20  62.090  51.7200  61.030  118470679
2025-05-30  60.76  63.850  50.7632  51.480  137772898
2025-06-30  51.19  51.400  47.3300  49.070  154739939
2025-07-31  49.07  49.855  45.2200  45.330  153335923
2025-08-08  45.37  47.470  45.0500  46.185   33776501


--- CPRT MARKET CAP TIME SERIES ---
Using quarterly shares outstanding data from 2005-04-30 to 2025-04-30
Shape: (309, 3)
Date range: 1999-12-31 to 2025-08-08
Current market cap: $45,173,040,465

Sample data (last 5 months):


close_price  shares_outstanding    market_cap
date                                                     
2025-04-30       61.030         978089000.0  5.969277e+10
2025-05-30       51.480         978089000.0  5.035202e+10
2025-06-30       49.070         978089000.0  4.799483e+10
2025-07-31       45.330         978089000.0  4.433677e+10
2025-08-08       46.185         978089000.0  4.517304e+10


SUMMARY OF ALL TIME SERIES DATA

AAPL:
  income_statement: 81 periods, 26 metrics
    Date range: 2005-06-30 to 2025-06-30
  balance_sheet: 81 periods, 38 metrics
    Date range: 2005-06-30 to 2025-06-30
  cash_flow: 81 periods, 29 metrics
    Date range: 2005-06-30 to 2025-06-30
  price_data: 309 months, 5 metrics
    Date range: 1999-12-31 to 2025-08-08
  market_cap: 309 months
    Date range: 1999-12-31 to 2025-08-08
    Latest market cap: $3,428,364,853,650

MSFT:
  income_statement: 81 periods, 26 metrics
    Date range: 2005-06-30 to 2025-06-30
  balance_sheet: 81 periods, 38 metrics
    Date range: 2005-06-30 to 2025-06-30
  cash_flow: 81 periods, 29 metrics
    Date range: 2005-06-30 to 2025-06-30
  price_data: 309 months, 5 metrics
    Date range: 1999-12-31 to 2025-08-08
  market_cap: 309 months
    Date range: 1999-12-31 to 2025-08-08
    Latest market cap: $3,897,028,600,000

GOOG:
  income_statement: 81 periods, 26 metrics
    Date range: 2005-06-30 to 2025-06-30
  balanc

In [61]:
# Merge all data into two comprehensive DataFrames: Quarterly and Monthly
print("="*80)
print("MERGING DATA INTO COMPREHENSIVE DATAFRAMES")
print("="*80)

def create_quarterly_master_df(financial_dataframes):
    """Merge all quarterly financial statements into one DataFrame with calendar quarter alignment"""
    quarterly_dfs = []
    
    def map_to_calendar_quarter(date):
        """Map a date to calendar quarter (Q1: Jan-Mar, Q2: Apr-Jun, etc.)"""
        year = date.year
        month = date.month
        if month <= 3:
            return pd.Timestamp(f"{year}-03-31")  # Q1 end
        elif month <= 6:
            return pd.Timestamp(f"{year}-06-30")  # Q2 end
        elif month <= 9:
            return pd.Timestamp(f"{year}-09-30")  # Q3 end
        else:
            return pd.Timestamp(f"{year}-12-31")  # Q4 end
    
    for symbol in financial_dataframes.keys():
        symbol_data = {}
        
        # Get all quarterly data for this symbol
        for statement_type, df in financial_dataframes[symbol].items():
            if not df.empty:
                # Add symbol and statement type prefix to columns
                prefixed_df = df.copy()
                
                # Remove reportType column as it's redundant (all quarterly)
                if 'reportType' in prefixed_df.columns:
                    prefixed_df = prefixed_df.drop('reportType', axis=1)
                
                # Map fiscal dates to calendar quarters
                prefixed_df['calendar_quarter'] = prefixed_df.index.map(map_to_calendar_quarter)
                
                # Add symbol AND statement type prefix to all columns to avoid conflicts
                statement_abbrev = {
                    'income_statement': 'IS',
                    'balance_sheet': 'BS', 
                    'cash_flow': 'CF'
                }
                abbrev = statement_abbrev.get(statement_type, statement_type.upper())
                prefixed_df.columns = [f"{symbol}_{abbrev}_{col}" if col != 'calendar_quarter' else col 
                                     for col in prefixed_df.columns]
                
                # Group by calendar quarter and take the latest report per quarter
                # (in case multiple reports fall in the same calendar quarter)
                grouped = prefixed_df.groupby('calendar_quarter').last()
                
                # Store in symbol_data dict
                symbol_data[statement_type] = grouped
        
        # Merge all statement types for this symbol by calendar quarter
        if symbol_data:
            symbol_combined = None
            for statement_type, df in symbol_data.items():
                if symbol_combined is None:
                    symbol_combined = df
                else:
                    # Outer join to keep all calendar quarters from all statements
                    symbol_combined = symbol_combined.join(df, how='outer')
            
            if symbol_combined is not None:
                quarterly_dfs.append(symbol_combined)
    
    # Merge all symbols together
    if quarterly_dfs:
        quarterly_master = quarterly_dfs[0]
        for df in quarterly_dfs[1:]:
            quarterly_master = quarterly_master.join(df, how='outer')
        
        # Sort by calendar quarter date
        quarterly_master = quarterly_master.sort_index()
        
        return quarterly_master
    
    return pd.DataFrame()

def create_monthly_master_df(price_dataframes, market_cap_dataframes):
    """Merge all monthly price and market cap data into one DataFrame"""
    monthly_dfs = []
    
    for symbol in price_dataframes.keys():
        symbol_dfs = []
        
        # Add price data
        if symbol in price_dataframes and not price_dataframes[symbol].empty:
            price_df = price_dataframes[symbol].copy()
            # Add symbol prefix to columns
            price_df.columns = [f"{symbol}_price_{col}" for col in price_df.columns]
            symbol_dfs.append(price_df)
        
        # Add market cap data
        if symbol in market_cap_dataframes and not market_cap_dataframes[symbol].empty:
            market_cap_df = market_cap_dataframes[symbol].copy()
            # Add symbol prefix to columns  
            market_cap_df.columns = [f"{symbol}_mktcap_{col}" for col in market_cap_df.columns]
            symbol_dfs.append(market_cap_df)
        
        # Combine price and market cap for this symbol
        if symbol_dfs:
            symbol_combined = symbol_dfs[0]
            for df in symbol_dfs[1:]:
                symbol_combined = symbol_combined.join(df, how='outer')
            
            monthly_dfs.append(symbol_combined)
    
    # Merge all symbols together
    if monthly_dfs:
        monthly_master = monthly_dfs[0]
        for df in monthly_dfs[1:]:
            monthly_master = monthly_master.join(df, how='outer')
        
        # Sort by date
        monthly_master = monthly_master.sort_index()
        
        return monthly_master
    
    return pd.DataFrame()

# Create the master DataFrames
print("\nCreating Calendar Quarter-Aligned Master DataFrame...")
quarterly_master_df = create_quarterly_master_df(financial_dataframes)

print("\nCreating Monthly Master DataFrame...")
monthly_master_df = create_monthly_master_df(price_dataframes, market_cap_dataframes)

# Display summary information
print("\n" + "="*80)
print("MASTER DATAFRAMES SUMMARY")
print("="*80)

if not quarterly_master_df.empty:
    print(f"\nQUARTERLY MASTER DATAFRAME (Calendar Quarter Aligned):")
    print(f"Shape: {quarterly_master_df.shape}")
    print(f"Date range: {quarterly_master_df.index.min().strftime('%Y-%m-%d')} to {quarterly_master_df.index.max().strftime('%Y-%m-%d')}")
    print(f"Total columns: {len(quarterly_master_df.columns)}")
    
    # Show calendar quarter alignment info
    print(f"\nCalendar quarters available: {len(quarterly_master_df.index)}")
    print("Quarter-end dates (latest 5):")
    for date in quarterly_master_df.index[-5:]:
        quarter_name = f"Q{(date.month-1)//3 + 1} {date.year}"
        print(f"  {date.strftime('%Y-%m-%d')} ({quarter_name})")
    
    # Show column breakdown by symbol and statement type
    print("\nColumns by symbol and statement:")
    symbols_in_quarterly = set()
    for col in quarterly_master_df.columns:
        symbol = col.split('_')[0]
        symbols_in_quarterly.add(symbol)
    
    for symbol in sorted(symbols_in_quarterly):
        symbol_cols = [col for col in quarterly_master_df.columns if col.startswith(f"{symbol}_")]
        print(f"  {symbol}: {len(symbol_cols)} columns")
    
    print(f"\nNon-null data points: {quarterly_master_df.notna().sum().sum():,}")
    print(f"Null data points: {quarterly_master_df.isna().sum().sum():,}")
    print(f"Data completeness: {quarterly_master_df.notna().sum().sum() / (quarterly_master_df.shape[0] * quarterly_master_df.shape[1]) * 100:.1f}%")
    
    print("\nSample data (last 3 calendar quarters, first 10 columns):")
    display(quarterly_master_df.tail(3).iloc[:, :10])

else:
    print("No quarterly data available")

if not monthly_master_df.empty:
    print(f"\nMONTHLY MASTER DATAFRAME:")
    print(f"Shape: {monthly_master_df.shape}")
    print(f"Date range: {monthly_master_df.index.min().strftime('%Y-%m-%d')} to {monthly_master_df.index.max().strftime('%Y-%m-%d')}")
    print(f"Total columns: {len(monthly_master_df.columns)}")
    
    # Show column breakdown by symbol and data type
    print("\nColumns by symbol and data type:")
    symbols_in_monthly = set()
    for col in monthly_master_df.columns:
        symbol = col.split('_')[0]
        symbols_in_monthly.add(symbol)
    
    for symbol in sorted(symbols_in_monthly):
        price_cols = [col for col in monthly_master_df.columns if col.startswith(f"{symbol}_price_")]
        mktcap_cols = [col for col in monthly_master_df.columns if col.startswith(f"{symbol}_mktcap_")]
        print(f"  {symbol}: {len(price_cols)} price columns, {len(mktcap_cols)} market cap columns")
    
    print(f"\nNon-null data points: {monthly_master_df.notna().sum().sum():,}")
    print(f"Null data points: {monthly_master_df.isna().sum().sum():,}")
    print(f"Data completeness: {monthly_master_df.notna().sum().sum() / (monthly_master_df.shape[0] * monthly_master_df.shape[1]) * 100:.1f}%")
    
    print("\nSample data (last 5 months, first 15 columns):")
    display(monthly_master_df.tail(5).iloc[:, :15])

else:
    print("No monthly data available")

print("\n" + "="*80)
print("DATA ACCESS EXAMPLES")
print("="*80)
print("# Access calendar quarter-aligned data:")
print("quarterly_master_df  # All quarterly financial data aligned to calendar quarters")
print("quarterly_master_df['AAPL_IS_totalRevenue']  # Apple's quarterly revenue by calendar quarter")
print("quarterly_master_df['MSFT_BS_totalAssets']  # Microsoft's total assets by calendar quarter")
print("quarterly_master_df['NVDA_CF_operatingCashflow']  # NVIDIA's operating cash flow by calendar quarter")
print("quarterly_master_df.filter(regex='^AAPL_')  # All Apple quarterly data")
print("quarterly_master_df.filter(regex='_IS_')  # All income statement data")
print("quarterly_master_df.loc['2024-12-31']  # All companies' Q4 2024 data")
print()
print("# Access monthly data:")
print("monthly_master_df  # All monthly price and market cap data") 
print("monthly_master_df['AAPL_price_close']  # Apple's monthly closing prices")
print("monthly_master_df['AAPL_mktcap_market_cap']  # Apple's monthly market cap")
print("monthly_master_df.filter(regex='^AAPL_')  # All Apple monthly data")
print()
print("# Cross-analysis examples:")
print("# Now quarterly and monthly data can be easily aligned!")
print("quarterly_master_df.loc['2024-12-31']  # Q4 2024 financials for all companies")
print("monthly_master_df.loc['2024-12-31']    # December 2024 prices for all companies")
print("# Calculate price-to-sales ratios, P/E ratios, etc. with aligned timeframes")

# Clean up column names summary for easier reference
print("\n" + "="*80)
print("COLUMN REFERENCE GUIDE")
print("="*80)

if not quarterly_master_df.empty:
    print("\nQUARTERLY COLUMNS (Calendar Quarter Aligned - sample):")
    sample_cols = list(quarterly_master_df.columns)[:15]  # First 15 columns
    for i, col in enumerate(sample_cols, 1):
        print(f"  {i:2d}. {col}")
    if len(quarterly_master_df.columns) > 15:
        print(f"  ... and {len(quarterly_master_df.columns) - 15} more columns")
    
    # Show breakdown by statement type
    print("\nColumns by statement type:")
    is_cols = [col for col in quarterly_master_df.columns if '_IS_' in col]
    bs_cols = [col for col in quarterly_master_df.columns if '_BS_' in col] 
    cf_cols = [col for col in quarterly_master_df.columns if '_CF_' in col]
    print(f"  Income Statement (IS): {len(is_cols)} columns")
    print(f"  Balance Sheet (BS): {len(bs_cols)} columns") 
    print(f"  Cash Flow (CF): {len(cf_cols)} columns")
    
    print("\nCalendar Quarter Standardization:")
    print("  • All fiscal reporting dates mapped to standard calendar quarters")
    print("  • Q1: Jan-Mar (ends 03-31), Q2: Apr-Jun (ends 06-30)")
    print("  • Q3: Jul-Sep (ends 09-30), Q4: Oct-Dec (ends 12-31)")
    print("  • Latest report taken if multiple reports per calendar quarter")

if not monthly_master_df.empty:
    print("\nMONTHLY COLUMNS:")
    for i, col in enumerate(monthly_master_df.columns, 1):
        print(f"  {i:2d}. {col}")

print("\n" + "="*80)
print("DATAFRAMES READY FOR ANALYSIS!")
print("="*80)

MERGING DATA INTO COMPREHENSIVE DATAFRAMES

Creating Calendar Quarter-Aligned Master DataFrame...

Creating Monthly Master DataFrame...

MASTER DATAFRAMES SUMMARY

QUARTERLY MASTER DATAFRAME (Calendar Quarter Aligned):
Shape: (82, 8280)
Date range: 2005-03-31 to 2025-06-30
Total columns: 8280

Calendar quarters available: 82
Quarter-end dates (latest 5):
  2024-06-30 (Q2 2024)
  2024-09-30 (Q3 2024)
  2024-12-31 (Q4 2024)
  2025-03-31 (Q1 2025)
  2025-06-30 (Q2 2025)

Columns by symbol and statement:
  AAPL: 90 columns
  ADBE: 90 columns
  ADI: 90 columns
  ADP: 90 columns
  ADSK: 90 columns
  AEP: 90 columns
  ALGN: 90 columns
  AMAT: 90 columns
  AMD: 90 columns
  AMGN: 90 columns
  AMZN: 90 columns
  ANSS: 90 columns
  ASML: 90 columns
  AVGO: 90 columns
  AZN: 90 columns
  BIDU: 90 columns
  BIIB: 90 columns
  BKNG: 90 columns
  BKR: 90 columns
  CDNS: 90 columns
  CEG: 90 columns
  CHTR: 90 columns
  CMCSA: 90 columns
  COST: 90 columns
  CPRT: 90 columns
  CRWD: 90 columns
  CSCO

AAPL_IS_reportedCurrency  AAPL_IS_grossProfit  \
calendar_quarter                                                  
2024-12-31                             NaN         5.827500e+10   
2025-03-31                             NaN         4.486700e+10   
2025-06-30                             NaN         4.371800e+10   

                  AAPL_IS_totalRevenue  AAPL_IS_costOfRevenue  \
calendar_quarter                                                
2024-12-31                1.243000e+11           6.602500e+10   
2025-03-31                9.535900e+10           5.049200e+10   
2025-06-30                9.403600e+10           5.031800e+10   

                  AAPL_IS_costofGoodsAndServicesSold  AAPL_IS_operatingIncome  \
calendar_quarter                                                                
2024-12-31                              6.602500e+10             4.283200e+10   
2025-03-31                              5.049200e+10             2.958900e+10   
2025-06-30                              5.031800e+10             2.820200e+10   

                  AAPL_IS_sellingGeneralAndAdministrative  \
calendar_quarter                                            
2024-12-31                                   7.175000e+09   
2025-03-31                                   6.728000e+09   
2025-06-30                                   6.650000e+09   

                  AAPL_IS_researchAndDevelopment  AAPL_IS_operatingExpenses  \
calendar_quarter                                                              
2024-12-31                          8.268000e+09               1.544300e+10   
2025-03-31                          8.550000e+09               1.527800e+10   
2025-06-30                          8.866000e+09               1.551600e+10   

                  AAPL_IS_investmentIncomeNet  
calendar_quarter                               
2024-12-31                                NaN  
2025-03-31                                NaN  
2025-06-30                                NaN


MONTHLY MASTER DATAFRAME:
Shape: (310, 741)
Date range: 1999-12-31 to 2025-08-08
Total columns: 741

Columns by symbol and data type:
  AAPL: 5 price columns, 3 market cap columns
  ADBE: 5 price columns, 3 market cap columns
  ADI: 5 price columns, 3 market cap columns
  ADP: 5 price columns, 3 market cap columns
  ADSK: 5 price columns, 3 market cap columns
  AEP: 5 price columns, 3 market cap columns
  ALGN: 5 price columns, 3 market cap columns
  AMAT: 5 price columns, 3 market cap columns
  AMD: 5 price columns, 3 market cap columns
  AMGN: 5 price columns, 3 market cap columns
  AMZN: 5 price columns, 3 market cap columns
  ANSS: 5 price columns, 3 market cap columns
  ASML: 5 price columns, 3 market cap columns
  AVGO: 5 price columns, 3 market cap columns
  AZN: 5 price columns, 3 market cap columns
  BIDU: 5 price columns, 3 market cap columns
  BIIB: 5 price columns, 3 market cap columns
  BKNG: 5 price columns, 3 market cap columns
  BKR: 5 price columns, 3 market cap colum

AAPL_price_open  AAPL_price_high  AAPL_price_low  \
date                                                           
2025-05-30          209.080           214.56        193.2500   
2025-06-30          200.280           207.39        195.0700   
2025-07-17              NaN              NaN             NaN   
2025-07-31          206.665           216.23        206.1401   
2025-08-08          210.865           231.00        201.5000   

            AAPL_price_close  AAPL_price_volume  AAPL_mktcap_close_price  \
date                                                                       
2025-05-30            200.85       1.195890e+09                   200.85   
2025-06-30            205.17       1.100504e+09                   205.17   
2025-07-17               NaN                NaN                      NaN   
2025-07-31            207.57       1.079936e+09                   207.57   
2025-08-08            229.35       5.362608e+08                   229.35   

            AAPL_mktcap_shares_outstanding  AAPL_mktcap_market_cap  \
date                                                                 
2025-05-30                    1.505613e+10            3.024024e+12   
2025-06-30                    1.494818e+10            3.066918e+12   
2025-07-17                             NaN                     NaN   
2025-07-31                    1.494818e+10            3.102794e+12   
2025-08-08                    1.494818e+10            3.428365e+12   

            MSFT_price_open  MSFT_price_high  MSFT_price_low  \
date                                                           
2025-05-30           431.11           462.52        424.9000   
2025-06-30           457.14           500.76        456.8900   
2025-07-17              NaN              NaN             NaN   
2025-07-31           496.47           555.45        488.7000   
2025-08-08           535.00           538.25        517.5511   

            MSFT_price_close  MSFT_price_volume  MSFT_mktcap_close_price  \
date                                                                       
2025-05-30            460.36        476961833.0                   460.36   
2025-06-30            497.41        401277780.0                   497.41   
2025-07-17               NaN                NaN                      NaN   
2025-07-31            533.50        396888800.0                   533.50   
2025-08-08            522.04        126464056.0                   522.04   

            MSFT_mktcap_shares_outstanding  
date                                        
2025-05-30                    7.461000e+09  
2025-06-30                    7.465000e+09  
2025-07-17                             NaN  
2025-07-31                    7.465000e+09  
2025-08-08                    7.465000e+09


DATA ACCESS EXAMPLES
# Access calendar quarter-aligned data:
quarterly_master_df  # All quarterly financial data aligned to calendar quarters
quarterly_master_df['AAPL_IS_totalRevenue']  # Apple's quarterly revenue by calendar quarter
quarterly_master_df['MSFT_BS_totalAssets']  # Microsoft's total assets by calendar quarter
quarterly_master_df['NVDA_CF_operatingCashflow']  # NVIDIA's operating cash flow by calendar quarter
quarterly_master_df.filter(regex='^AAPL_')  # All Apple quarterly data
quarterly_master_df.filter(regex='_IS_')  # All income statement data
quarterly_master_df.loc['2024-12-31']  # All companies' Q4 2024 data

# Access monthly data:
monthly_master_df  # All monthly price and market cap data
monthly_master_df['AAPL_price_close']  # Apple's monthly closing prices
monthly_master_df['AAPL_mktcap_market_cap']  # Apple's monthly market cap
monthly_master_df.filter(regex='^AAPL_')  # All Apple monthly data

# Cross-analysis examples:
# Now quarterly and monthly data can b

In [ ]:
pd.reset_option('display.max_rows')
pd.reset_option('display.max_columns')



In [ ]:
# Assuming quarterly_master_df is already defined
quarterly_master_df.to_excel('quarterly_master_df.xlsx', index=True)  
monthly_master_df.to_excel('month_master_df.xlsx', index=True)  


In [ ]:
quarterly_master_df

AAPL_IS_reportedCurrency  AAPL_IS_grossProfit  \
calendar_quarter                                                  
2005-03-31                             NaN                  NaN   
2005-06-30                             NaN         1.044000e+09   
2005-09-30                             NaN         1.035000e+09   
2005-12-31                             NaN         1.564000e+09   
2006-03-31                             NaN         1.297000e+09   
...                                    ...                  ...   
2024-06-30                             NaN         3.967800e+10   
2024-09-30                             NaN         4.387900e+10   
2024-12-31                             NaN         5.827500e+10   
2025-03-31                             NaN         4.486700e+10   
2025-06-30                             NaN         4.371800e+10   

                  AAPL_IS_totalRevenue  AAPL_IS_costOfRevenue  \
calendar_quarter                                                
2005-03-31                         NaN                    NaN   
2005-06-30                3.520000e+09           2.476000e+09   
2005-09-30                3.678000e+09           2.643000e+09   
2005-12-31                5.749000e+09           4.185000e+09   
2006-03-31                4.359000e+09           3.062000e+09   
...                                ...                    ...   
2024-06-30                8.577700e+10           4.609900e+10   
2024-09-30                9.493000e+10           5.105100e+10   
2024-12-31                1.243000e+11           6.602500e+10   
2025-03-31                9.535900e+10           5.049200e+10   
2025-06-30                9.403600e+10           5.031800e+10   

                  AAPL_IS_costofGoodsAndServicesSold  AAPL_IS_operatingIncome  \
calendar_quarter                                                                
2005-03-31                                       NaN                      NaN   
2005-06-30                              2.476000e+09             4.260000e+08   
2005-09-30                              2.643000e+09             4.180000e+08   
2005-12-31                              4.185000e+09             7.500000e+08   
2006-03-31                              3.062000e+09             5.290000e+08   
...                                              ...                      ...   
2024-06-30                              4.609900e+10             2.535200e+10   
2024-09-30                              5.105100e+10             2.959100e+10   
2024-12-31                              6.602500e+10             4.283200e+10   
2025-03-31                              5.049200e+10             2.958900e+10   
2025-06-30                              5.031800e+10             2.820200e+10   

                  AAPL_IS_sellingGeneralAndAdministrative  \
calendar_quarter                                            
2005-03-31                                            NaN   
2005-06-30                                   4.720000e+08   
2005-09-30                                   4.700000e+08   
2005-12-31                                   6.320000e+08   
2006-03-31                                   5.920000e+08   
...                                                   ...   
2024-06-30                                   6.320000e+09   
2024-09-30                                   6.523000e+09   
2024-12-31                                   7.175000e+09   
2025-03-31                                   6.728000e+09   
2025-06-30                                   6.650000e+09   

                  AAPL_IS_researchAndDevelopment  AAPL_IS_operatingExpenses  \
calendar_quarter                                                              
2005-03-31                                   NaN                        NaN   
2005-06-30                          1.450000e+08               6.180000e+08   
2005-09-30                          1.470000e+08               6.170000e+08   
2005-12-31                          1.820000e+08         

In [ ]:
monthly_master_df

AAPL_price_open  AAPL_price_high  AAPL_price_low  \
date                                                           
1999-12-31          101.000           118.00         91.0600   
2000-01-31          104.870           121.50         86.5000   
2000-02-29          104.000           119.94         97.0000   
2000-03-31          118.560           150.38        114.0000   
2000-04-28          135.500           139.50        104.8700   
...                     ...              ...             ...   
2025-05-30          209.080           214.56        193.2500   
2025-06-30          200.280           207.39        195.0700   
2025-07-17              NaN              NaN             NaN   
2025-07-31          206.665           216.23        206.1401   
2025-08-08          210.865           231.00        201.5000   

            AAPL_price_close  AAPL_price_volume  AAPL_mktcap_close_price  \
date                                                                       
1999-12-31            102.81       8.409120e+07                   102.81   
2000-01-31            103.75       1.120998e+08                   103.75   
2000-02-29            114.62       6.535520e+07                   114.62   
2000-03-31            135.81       7.766390e+07                   135.81   
2000-04-28            124.06       7.734290e+07                   124.06   
...                      ...                ...                      ...   
2025-05-30            200.85       1.195890e+09                   200.85   
2025-06-30            205.17       1.100504e+09                   205.17   
2025-07-17               NaN                NaN                      NaN   
2025-07-31            207.57       1.079936e+09                   207.57   
2025-08-08            229.35       5.362608e+08                   229.35   

            AAPL_mktcap_shares_outstanding  AAPL_mktcap_market_cap  \
date                                                                 
1999-12-31                    2.410248e+10            2.477976e+12   
2000-01-31                    2.410248e+10            2.500633e+12   
2000-02-29                    2.410248e+10            2.762627e+12   
2000-03-31                    2.410248e+10            3.273358e+12   
2000-04-28                    2.410248e+10            2.990154e+12   
...                                    ...                     ...   
2025-05-30                    1.505613e+10            3.024024e+12   
2025-06-30                    1.494818e+10            3.066918e+12   
2025-07-17                             NaN                     NaN   
2025-07-31                    1.494818e+10            3.102794e+12   
2025-08-08                    1.494818e+10            3.428365e+12   

            MSFT_price_open  MSFT_price_high  ...  \
date                                          ...   
1999-12-31            91.06           119.94  ...   
2000-01-31           117.37           118.62  ...   
2000-02-29            98.50           110.00  ...   
2000-03-31            89.62           115.00  ...   
2000-04-28            94.44            96.50  ...   
...                     ...              ...  ...   
2025-05-30           431.11           462.52  ...   
2025-06-30           457.14           500.76  ...   
2025-07-17              NaN              NaN  ...   
2025-07-31           496.47           555.45  ...   
2025-08-08           535.00           538.25  ...   

            DXCM_mktcap_shares_outstanding  DXCM_mktcap_market_cap  \
date                                                                 
1999-12-31                             NaN                     NaN   
2000-01-31                             NaN                     NaN   
2000-02-29                             NaN                     NaN   
2000-03-31                             NaN                     NaN   
2000-04-28                             NaN                     NaN   
...                                    ...                     ...   
2025-05-30                   

In [ ]:
''''list of symbols are producing: timeseries of income statement, balance sheet, and cash flow statement from this take:

Fundamentals / valuation
Price (close), 12-month high, 12-month low (for price_range).
Shares outstanding, MarketCap = price × shares.
Total Enterprise Value (TEV) = Market Cap + Total Debt − Cash & equivalents.
Book value of equity (book value) → Book-to-Market (B/M) = Book / MarketCap.
Free cash flow (FCF) = Operating cash flow − Capital expenditures (capex).
FCF/P (free cash flow yield) = FCF / MarketCap (paper calls FCF/P free cash flow yield). 
BCU Open Access
EBITDA, revenue, operating profit.
ROA = Net income / Total assets.
EBITDA margin = EBITDA / Revenue.
Assets (total assets) and YoY asset growth % = (Assets_t − Assets_{t−1}) / Assets_{t−1}.
EBITDA YoY growth % = (EBITDA_t − EBITDA_{t−1}) / EBITDA_{t−1}.
Net income, EPS (but note EPS not used as primary predictor).
Debt-to-equity, Total debt, Interest expense (for coverage)
EV/EBITDA, EV/Sales (optional).
Insiders transactions (sum net buys/sells last 12 months).
Institutional ownership %, analyst coverage (optional).

3) Hard filters (exclude these immediately) — follow the paper’s strong findings
(These are must apply before scoring.)
Inv_dummy == 1 → EXCLUDE (paper: huge negative effect ≈ −22.8 p.p.). If you prefer not to exclude, apply a heavyweight penalty (score −2 or weight multiplier). 
BCU Open Access
Remove firms with missing or zero MarketCap / TEV data.
Remove micro-penny, illiquid names — set min ADV (average daily volume) threshold (e.g., 50k–100k shares/day) and/or min price (e.g., $1) to avoid stale quotes and microstructure issues. (Paper uses listed major exchanges.)
If using P/E at all: only for firms with positive, stable earnings for last 2 yrs (paper: P/E is unreliable and was avoided). Prefer FCF/P/BM instead.
''''



SyntaxError: invalid syntax (280134358.py, line 1)

In [ ]:
import pandas as pd

# note to self, goed de methodologie en redenen van berekeningen snappen, price range bv is voor een rede daar niet puur arbitraire POEP




In [59]:
# Price (close) - Extract all symbols from existing columns
# Get all unique symbols from column names that follow the pattern {SYMBOL}_price_close
symbols = []
for col in quarterly_master_df.columns:
    if col.endswith('_price_close'):
        symbol = col.replace('_price_close', '')
        symbols.append(symbol)

print(f"Found symbols: {symbols}")

# Create a new DataFrame to hold the price close and price range
price_data = pd.DataFrame()

for symbol in symbols:
    # Extract price close for the symbol (assuming the column exists)
    close_col = f'{symbol}_price_close'
    high_col = f'{symbol}_price_high'
    low_col = f'{symbol}_price_low'
    
    if close_col in quarterly_master_df.columns:
        price_data[f'{symbol}_price_close'] = quarterly_master_df[close_col]
        
        # Calculate price range using high and low if available
        if high_col in quarterly_master_df.columns and low_col in quarterly_master_df.columns:
            price_data[f'{symbol}_price_range'] = quarterly_master_df[high_col] - quarterly_master_df[low_col]
            price_data[f'{symbol}_price_high'] = quarterly_master_df[high_col]
            price_data[f'{symbol}_price_low'] = quarterly_master_df[low_col]
        else:
            # If high/low columns don't exist, calculate rolling high/low from close prices
            price_data[f'{symbol}_price_high'] = quarterly_master_df[close_col].rolling(window=4).max()
            price_data[f'{symbol}_price_low'] = quarterly_master_df[close_col].rolling(window=4).min()
            price_data[f'{symbol}_price_range'] = price_data[f'{symbol}_price_high'] - price_data[f'{symbol}_price_low']

# Reset index to ensure clean DataFrame
price_data = price_data.reset_index(drop=True)

# Display the new DataFrame
print(f"Price data shape: {price_data.shape}")
print(f"Columns: {list(price_data.columns)}")
display(price_data.tail(10))

Found symbols: []
Price data shape: (0, 0)
Columns: []


Empty DataFrame
Columns: []
Index: []

In [60]:
price_data

Empty DataFrame
Columns: []
Index: []

In [ ]:

# Shares outstanding (as floats)
deze cell bestaat gewoon

# MarketCap = price × shares_outstanding (fallback to provided MarketCapitalization)
deze bestaat ook 

# Total Debt
berekening ziet er dubieus uit, dubbelchecken
quarterly_master_df['total_debt'] = col('totalDebt','TotalDebt','shortLongTermDebtTotal','shortLongTermDebt','longTermDebt', numeric=True)

# Cash & equivalents
idem als hierboven
quarterly_master_df['cash_and_equivalents'] = col('cashAndCashEquivalentsAtCarryingValue','cashAndShortTermInvestments','cash_and_equivalents','cash', numeric=True)

# Total Enterprise Value (TEV) = Market Cap + Total Debt − Cash & equivalents

quarterly_master_df['enterprise_value'] = (
    quarterly_master_df['market_cap'] + quarterly_master_df['total_debt'] - quarterly_master_df['cash_and_equivalents']
)

# Book value of equity (book value)
quarterly_master_df['book_value_equity'] = col('totalShareholderEquity','totalStockholdersEquity','book_value','shareholder_equity', numeric=True)

# Book-to-Market (B/M) = Book / MarketCap
quarterly_master_df['book_to_market'] = quarterly_master_df['book_value_equity'] / quarterly_master_df['market_cap']

# Free cash flow (FCF) = Operating cash flow − Capital expenditures (capex)
operating_cf = col('operatingCashflow','netCashProvidedByOperatingActivities','operating_cash_flow', numeric=True)
capex = col('capitalExpenditures','capitalExpendituresFixedAssets','capex', numeric=True)
quarterly_master_df['free_cash_flow'] = operating_cf - capex

# FCF/P (free cash flow yield) = FCF / MarketCap
quarterly_master_df['fcf_yield'] = quarterly_master_df['free_cash_flow'] / quarterly_master_df['market_cap']

# EBITDA, revenue, operating profit
quarterly_master_df['ebitda'] = col('EBITDA','ebitda', numeric=True)
quarterly_master_df['revenue'] = col('totalRevenue','Revenue','revenue', numeric=True)
quarterly_master_df['operating_income'] = col('operatingIncome','OperatingIncome','operating_profit', numeric=True)

# ROA = Net income / Total assets
quarterly_master_df['roa'] = col('netIncome','NetIncome','net_income', numeric=True) / col('totalAssets','TotalAssets','assets','total_assets', numeric=True)

# EBITDA margin = EBITDA / Revenue
quarterly_master_df['ebitda_margin'] = quarterly_master_df['ebitda'] / quarterly_master_df['revenue']

# YoY asset growth % = (Assets_t − Assets_{t−1}) / Assets_{t−1}
assets = col('totalAssets','TotalAssets','assets','total_assets', numeric=True)
quarterly_master_df['asset_growth_yoy'] = assets.pct_change(periods=4)

# EBITDA YoY growth % = (EBITDA_t − EBITDA_{t−1}) / EBITDA_{t−1}
quarterly_master_df['ebitda_growth_yoy'] = quarterly_master_df['ebitda'].pct_change(periods=4)

# Net income, EPS (EPS may require shares; here EPS = Net income / shares)
ni = col('netIncome','NetIncome','net_income', numeric=True)
sh = quarterly_master_df['shares_outstanding']
quarterly_master_df['eps'] = ni / sh
quarterly_master_df['net_income'] = ni

# Debt-to-equity = Total debt / Book value of equity
quarterly_master_df['debt_to_equity'] = quarterly_master_df['total_debt'] / quarterly_master_df['book_value_equity']

# EV/EBITDA and EV/Sales
quarterly_master_df['ev_to_ebitda'] = quarterly_master_df['enterprise_value'] / quarterly_master_df['ebitda']
quarterly_master_df['ev_to_sales'] = quarterly_master_df['enterprise_value'] / quarterly_master_df['revenue']

# Insider transactions placeholder (requires separate data); keep column if exists
if 'insider_net_12m' not in quarterly_master_df.columns:
    quarterly_master_df['insider_net_12m'] = pd.NA

# Institutional ownership %, analyst coverage placeholders if missing
for name in ['institutional_ownership_pct','analyst_coverage']:
    if name not in quarterly_master_df.columns:
        quarterly_master_df[name] = pd.NA

# Optional: ensure time index is preserved as a column before any export
if quarterly_master_df.index.name is None:
    quarterly_master_df.index.name = 'date'
quarterly_master_df.reset_index(inplace=True)

# 12-month high/low and range (4 periods ~ 12 months for quarterly data)
if 'date' in quarterly_master_df.columns:
    if 'symbol' in quarterly_master_df.columns:
        quarterly_master_df.sort_values(['symbol','date'], inplace=True)
        quarterly_master_df['price_12m_high'] = quarterly_master_df.groupby('symbol')['price'].transform(lambda s: s.rolling(4, min_periods=1).max())
        quarterly_master_df['price_12m_low'] = quarterly_master_df.groupby('symbol')['price'].transform(lambda s: s.rolling(4, min_periods=1).min())
    else:
        quarterly_master_df.sort_values('date', inplace=True)
        quarterly_master_df['price_12m_high'] = quarterly_master_df['price'].rolling(4, min_periods=1).max()
        quarterly_master_df['price_12m_low'] = quarterly_master_df['price'].rolling(4, min_periods=1).min()
    quarterly_master_df['price_range_12m'] = quarterly_master_df['price_12m_high'] - quarterly_master_df['price_12m_low']



